In [1]:
import pandas as pd
import numpy as np

In [2]:
df = pd.read_excel('/content/drive/My Drive/Colab Notebooks/hackathon_ml/ENB2012_data.xlsx')
df.columns = ['relative_compactness', 'surface_area', 'wall_area', 'roof_area', 'overall_height','orientation', 'glazing_area', 'glazing_area_distribution', 'heating_load', 'cooling_load']
df.head()

relative_compactness  surface_area  ...  heating_load  cooling_load
0                  0.98         514.5  ...         15.55         21.33
1                  0.98         514.5  ...         15.55         21.33
2                  0.98         514.5  ...         15.55         21.33
3                  0.98         514.5  ...         15.55         21.33
4                  0.90         563.5  ...         20.84         28.28

[5 rows x 10 columns]

In [3]:
!pip install pandas-visual-analysis


In [4]:
from pandas_visual_analysis import VisualAnalysis

In [5]:
df.isna().sum()

relative_compactness         0
surface_area                 0
wall_area                    0
roof_area                    0
overall_height               0
orientation                  0
glazing_area                 0
glazing_area_distribution    0
heating_load                 0
cooling_load                 0
dtype: int64

In [6]:
!pip install pandas-profiling==2.9.0

In [27]:
import pandas_profiling
pandas_profiling.ProfileReport(df)

In [8]:
dum = pd.get_dummies(df.glazing_area_distribution, prefix='glazing_area_distribution_level')

In [11]:
dum.drop(['glazing_area_distribution_level_5'],axis=1,inplace=True)

In [12]:
dum

glazing_area_distribution_level_0  ...  glazing_area_distribution_level_4
0                                    1  ...                                  0
1                                    1  ...                                  0
2                                    1  ...                                  0
3                                    1  ...                                  0
4                                    1  ...                                  0
..                                 ...  ...                                ...
763                                  0  ...                                  0
764                                  0  ...                                  0
765                                  0  ...                                  0
766                                  0  ...                                  0
767                                  0  ...                                  0

[768 rows x 5 columns]

In [14]:
features = df.drop(['heating_load','cooling_load'], axis=1)
labels = df.iloc[:,8:]

In [15]:
features.drop(['glazing_area_distribution'],axis=1,inplace=True)

In [16]:
features

relative_compactness  surface_area  ...  orientation  glazing_area
0                    0.98         514.5  ...            2           0.0
1                    0.98         514.5  ...            3           0.0
2                    0.98         514.5  ...            4           0.0
3                    0.98         514.5  ...            5           0.0
4                    0.90         563.5  ...            2           0.0
..                    ...           ...  ...          ...           ...
763                  0.64         784.0  ...            5           0.4
764                  0.62         808.5  ...            2           0.4
765                  0.62         808.5  ...            3           0.4
766                  0.62         808.5  ...            4           0.4
767                  0.62         808.5  ...            5           0.4

[768 rows x 7 columns]

In [17]:

labels.head()

heating_load  cooling_load
0         15.55         21.33
1         15.55         21.33
2         15.55         21.33
3         15.55         21.33
4         20.84         28.28

In [22]:
from sklearn.preprocessing import StandardScaler
scaler = StandardScaler()
scaler.fit(features)
scaled_transformed = scaler.transform(features)

In [29]:
scaled_features = pd.DataFrame(scaled_transformed,columns=['relative_compactness', 'surface_area' ,	'wall_area' ,'roof_area', 'overall_height' , 'orientation' ,'glazing_area'])

In [31]:
scaled_features = scaled_features.join(dum)

In [34]:
scaled_features.head()

relative_compactness  ...  glazing_area_distribution_level_4
0              2.041777  ...                                  0
1              2.041777  ...                                  0
2              2.041777  ...                                  0
3              2.041777  ...                                  0
4              1.284979  ...                                  0

[5 rows x 12 columns]

In [35]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(scaled_features, labels , random_state = 47)

In [36]:
from sklearn.ensemble import RandomForestRegressor
rf = RandomForestRegressor(random_state=47)
rf.fit(X_train, y_train)
y_pred = rf.predict(X_test)

In [37]:
from sklearn.metrics import mean_squared_error,r2_score 

In [38]:
print('mean squared error ',mean_squared_error(y_test,y_pred))
print('R2 score ',r2_score(y_test,y_pred))

mean squared error  2.34648527860522
R2 score  0.9755316584635254


### now comes hyper paramater tuning to further decrese the loss

In [40]:
from sklearn.model_selection import GridSearchCV

param_grid = {'max_depth' : [4,5,6,7,9],
              'min_samples_split': [10,11,12,14,16],
              'min_samples_leaf' : [3,4,5,6,7],
              'n_estimators': [40,50,60,70,80]
              }


gs_rf = GridSearchCV(rf, param_grid ,n_jobs=-1)
gs_rf.fit(X_train, y_train)
print(gs_rf.best_params_)
print(gs_rf.best_score_)

{'max_depth': 9, 'min_samples_leaf': 3, 'min_samples_split': 12, 'n_estimators': 80}
0.9795178786088543


In [42]:
y_pred = gs_rf.predict(X_test)

In [43]:
print('mean squared error ',mean_squared_error(y_test,y_pred))
print('R2 score ',r2_score(y_test,y_pred))

mean squared error  1.7430299297560792
R2 score  0.9819653964297871
